# Combined clustering & merging pipeline


### Modules

In [1]:
# Python modules
import os
import sys
%load_ext autoreload
%autoreload 2
# Python modules
import os
import sys

# Get the directory of the current script
script_dir = os.path.dirname(os.path.abspath("combined_pipeline (1).ipynb"))

# Define relative paths to your module directories
relative_paths = [
    os.path.join(script_dir, "DistantSigMA"),
    os.path.join(script_dir, "DistantSigMA", "alex_workspace")
]

# Append the relative paths to sys.path
for path in relative_paths:
    if path not in sys.path:
        sys.path.append(path)
       
sys.path.append(r'C:\Users\Alexm\OneDrive - Universität Wien\01_WINF\Praktikum1\Git2\Distant_SigMA')
import warnings
warnings.filterwarnings('ignore')

#### DistantSigMA modules
from misc import utilities as ut
from DistantSigMA.clustering_routine import *
from DistantSigMA.DistantSigMA.cluster_simulations import calculate_std_devs
from DistantSigMA.DistantSigMA.scalefactor_sampling import lhc_lloyd

# Tree/Graph modules
from alex_workspace.ClusterHandler import ClusteringHandler
from alex_workspace.NxGraphAssistant import NxGraphAssistant
from alex_workspace.PlotHandler import PlotHandler
from alex_workspace.Tree import Custom_Tree

## Setup

In [2]:
# Paths
output_path = ut.set_output_path(script_name="combined_pipeline")

run = "combined_pipe_box_0"
output_path = output_path + f"{run}/"
if not os.path.exists(output_path):
    os.makedirs(output_path)

## Data

In [4]:
# load the dataframe
df_load = pd.read_csv(r"C:\Users\Alexm\OneDrive - Universität Wien\01_WINF\Praktikum1\Git2\Distant_SigMA\DistantSigMA\DistantSigMA\Data/Box_1.csv")
# Add new columns with value 1

# df_load= df_load.reset_index(drop=True)


# load data for error sampling (already slimmed)
error_sampling_df = pd.read_csv(r"C:\Users\Alexm\OneDrive - Universität Wien\01_WINF\Praktikum1\Git2\Distant_SigMA\DistantSigMA\DistantSigMA\Data/Gaia_DR3_1000pc_rs.csv")
#error_sampling_df.to_csv("../Data/Gaia/Gaia_DR3_1000pc_rs.csv")
error_sampling_df["dist"] = 1000 / error_sampling_df["parallax"]

### Choosing data chunks

## Clustering

Currently written for the scenario that the input is a single chunk without need for further splitting.

### A) Preliminary solution

In [5]:
# Cluster parameters
dict_prelim = dict(alpha=0.05,
                   beta=0.99,
                   knn_initcluster_graph=35,
                   KNN_list=[15, 20, 25],
                   sfs=[0.15, 0.2, 0.3],
                   scaling="robust",
                   bh_correction=True)

In [33]:
import time
from functools import wraps

def retry_on_error(max_attempts=3, delay=1):
    def decorator(func):
            def wrapper(*args, **kwargs):
                attempts = 0
                while attempts < max_attempts:
                    try:
                        return func(*args, **kwargs)
                    except Exception as e:
                        print(f"Error occurred: {e}")
                        print(f"Retrying... (Attempt {attempts + 1} of {max_attempts})")
                        attempts += 1
                        time.sleep(delay)
                raise Exception(f"Function {func.__name__} failed after {max_attempts} attempts")
            return wrapper
    return decorator

@retry_on_error(max_attempts=10, delay=2)
def run_clustering_and_simulation(chunk, df_chunk, result_path, dict_prelim, error_sampling_df):
    print(f"PART A) Starting clustering ... \n")
    df_prelim = run_clustering(region_label=chunk, df_input=df_chunk, sf_params="parallax_scaled",
                               parameter_dict=dict_prelim, mode="prelim", output_loc=result_path)
    
    print(f"PART B) Simulating clusters ... \n")
    stds = calculate_std_devs(input_df=df_prelim, SigMA_dict=dict_prelim, sampling_data= error_sampling_df, n_artificial = 1, sample_radius= 10, output_path = result_path, plot_figs = False)

    
    return df_prelim, stds

# Main execution block
try:
    chunk = 0
    df_chunk = df_load
    result_path = output_path

    df_prelim, stds = run_clustering_and_simulation(chunk, df_chunk, result_path, dict_prelim, error_sampling_df)

    # save scaling factors in Data directory
    directory = r"C:\Users\Alexm\OneDrive - Universität Wien\01_WINF\Praktikum1\Git2\Distant_SigMA\DistantSigMA\DistantSigMA\Data/Scale_factors"
    filename = f"sfs_region_{chunk}.txt"

    # Open the file in write mode ('w')
    with open(f"{directory}/{filename}", 'w') as file:
        for i, label in enumerate(["ra", "dec", "parallax", "pmra", "pmdec"]):
            print(f"{label}:", np.min(stds[i, :]), np.mean(stds[i, :]), np.max(stds[i, :]), file=file)
except Exception as e:
    print(f"An error occurred during the entire process: {e}")

PART A) Starting clustering ... 

-- Current run with KNN = 15 -- 

Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.1...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 1.00e-05
Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.15...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 1.00e-05
Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.2...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 1.00e-05
Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.25...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 1.00e-05
Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.3...
Performing gradient ascend using a 15-NN density estimation.
Update

In [6]:
chunk = 0
df_chunk = df_load
result_path = output_path

print(f"PART A) Starting clustering ... \n")

df_prelim = run_clustering(region_label=chunk, df_input=df_chunk, sf_params="parallax_scaled",
                           parameter_dict=dict_prelim, mode="prelim", output_loc=result_path)

PART A) Starting clustering ... 

-- Current run with KNN = 15 -- 

Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.15...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 5.42e-04
Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.2...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 5.42e-04
Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.3...
Performing gradient ascend using a 15-NN density estimation.
Updated significance threshold: 5.42e-04
:: Finished run for KNN=15! 
. Found 2 / 2 / 4 final clusters.
-- Current run with KNN = 20 -- 

Creating k-d trees of resampled data sets...
Performing clustering for scale factor 0.15...
Performing gradient ascend using a 20-NN density estimation.
Updated significance threshold: 8.20e-05
Creating k-d trees of resampled data sets...
Performing clust

### B) Simulate clusters and determine scale factors

In [10]:
print(f"PART B) Simulating clusters ... \n")

stds = calculate_std_devs(input_df=df_prelim, SigMA_dict=dict_prelim, sampling_data= error_sampling_df, n_artificial = 1, sample_radius= 100, output_path = result_path, plot_figs = False)

# save scaling factors in Data directory
# save scaling factors in Data directory
directory = r"C:\Users\Alexm\OneDrive - Universität Wien\01_WINF\Praktikum1\Git2\Distant_SigMA\DistantSigMA\DistantSigMA\Data/Scale_factors"
filename = f"sfs_region_{chunk}.txt"

# Open the file in write mode ('w')
with open(f"{directory}/{filename}", 'w') as file:
    for i, label in enumerate(["ra", "dec", "parallax", "pmra", "pmdec"]):
        print(f"{label}:", np.min(stds[i, :]), np.mean(stds[i, :]), np.max(stds[i, :]), file=file)

PART B) Simulating clusters ... 

Negative values encountered in resampled parallax column.Removed 1930 samples.
Negative values encountered in resampled parallax column.Removed 29 samples.
Negative values encountered in resampled parallax column.Removed 1 samples.


### C) Cluster with new SF

In [11]:
# determine the number of SF to draw using lhc_lloyd sampling
num_sf = 40

In [12]:
# draw number of scale factors
sfs, means = lhc_lloyd(r'C:\Users\Alexm\OneDrive - Universität Wien\01_WINF\Praktikum1\Git2\Distant_SigMA\DistantSigMA\DistantSigMA\Data/Scale_factors/' + f'sfs_region_{chunk}.txt', num_sf)

# determine means for clusterer initialization
scale_factor_means = {'pos': {'features': ['ra', 'dec', 'parallax'], 'factor': list(means[:3])},
                      'vel': {'features': ['pmra', 'pmdec'], 'factor': list(means[3:])}}

# dict for final clustering
dict_final = dict(alpha=0.05,
                  beta=0.99,
                  knn_initcluster_graph=35,
                  KNN_list=[20],
                  sfs=sfs,
                  scaling=None,
                  bh_correction=True)

# Generate grouped solutions
grouped_labels = partial_clustering(df_input=df_chunk, sf_params=["ra", "dec", "parallax", "pmra", "pmdec"], parameter_dict=dict_final, mode="final",output_loc=result_path, column_means=scale_factor_means)

print(grouped_labels.shape)
# add the grouped solution labels to the dataframe holding the observations
df_final = df_chunk.copy()
for col in range(grouped_labels.shape[0]):
    df_final.loc[:, f"cluster_label_group_{col}"] = grouped_labels[col, :]

#df_final.to_csv(result_path+f"Region_{chunk}_sf_{num_sf}_grouped_solutions.csv")

-- Current run with KNN = 20 -- 

Creating k-d trees of resampled data sets...
Performing clustering for scale factor p[0.546929776822896, 0.2930325886917343, 1.4243203433109173][0.10779055136439505, 0.052268260451654884]...
Performing gradient ascend using a 20-NN density estimation.
Updated significance threshold: 8.21e-04
Creating k-d trees of resampled data sets...
Performing clustering for scale factor p[0.35455817447834437, 0.9454923854824778, 1.2693224640075795][0.06990333455241186, 0.04361665233568033]...
Performing gradient ascend using a 20-NN density estimation.
Updated significance threshold: 2.22e-04
Creating k-d trees of resampled data sets...
Performing clustering for scale factor p[0.07216010168719379, 0.2328147169913543, 1.4150397157063435][0.07978662507642797, 0.07349809645286773]...
Performing gradient ascend using a 20-NN density estimation.
Updated significance threshold: 4.47e-04
Creating k-d trees of resampled data sets...
Performing clustering for scale factor p

### D) Tree/Graph

Below this point, the routine follows the minimal_usage.ipynb script from Alex.

In [13]:
# Creating instances of custom classes
clusterMaster = ClusteringHandler()  # Manages cluster operations


#### Graph handling

In [14]:
df_final["pmra_error"] = 1
df_final["pmdec_error"] = 1


In [15]:
# make consensus over the grouped labels that came out of step C)
cc = ClusterConsensus(*grouped_labels)  # creates graph object cc.G
translation = cc.labels_bool_dict2arr

#rename the similarity in every edge to "weight"
for i, j, d in cc.G.edges(data=True):
    d['weight'] = d['similarity']
    d['weight_minor'] = d['similarity_minor']
    del d['similarity']
    del d['similarity_minor']

In [21]:
import networkx as nx
#FIXME optimize me
# Jaccard (minor) distances
graph_base = cc.G.copy()

#plot graph_base
nx.draw(graph_base, with_labels=True)
graph = NxGraphAssistant.remove_edges_with_minor(graph_base, 'weight', 0.3, 0.7)

#FIXME optimize me
# Merging thresholds for cliques (inner average Jaccard distance)
graph = NxGraphAssistant.analyze_cliques(graph, 0.95)

plotter = PlotHandler(translation,df_final, "")
tree = clusterMaster.do_all(graph, Custom_Tree.alex_optimal)
for tree in tree:
    tree.print_tree()
    print("##################")
    

labels = clusterMaster.full_pipline_tree_hierachy(graph, Custom_Tree.alex_optimal, translation,plotter,2,1)



plotter.plot_labels_2D(labels)

1+4+8+11+14+16+19+23+26
##################
2+5+7+10+17+20+22+25
##################
13
##################


In [19]:
import itertools
from sklearn.metrics import normalized_mutual_info_score
from tqdm import tqdm
import matplotlib.pyplot as plt
from collections import defaultdict

def test_parameters(df_final, translation):
    # Define parameter ranges
    edge_removal_lower = list(np.arange(0.0, 0.5, 0.05))
    edge_removal_upper = list(np.arange(0.6, 1, 0.1))
    clique_merge = list(np.arange(0.6, 1, 0.05))
    cluster_distance = list(np.arange(0.5, 4, 0.5))
    tree_functions = [
        #Custom_Tree.problem_handler_create_multiple_trees_on_conflict,
        #Custom_Tree.alex_optimal_alternative,
        Custom_Tree.alex_optimal
    ]

    top_results = []
    best_nmi = float('-inf')  # Initialize best_nmi to negative infinity

    # Create a list of valid parameter combinations
    valid_combinations = [
        params for params in itertools.product(edge_removal_lower, edge_removal_upper, clique_merge, cluster_distance, tree_functions)
        if params[0] < params[1]
    ]

    # Use tqdm to create a progress bar
    for params in tqdm(valid_combinations, desc="Testing Parameters", unit="combination"):
        graph_base = cc.G.copy()
        graph = NxGraphAssistant.remove_edges_with_minor(
            graph_base, 'weight', 
            params[0],
            params[1]
        )

        graph = NxGraphAssistant.analyze_cliques(graph, params[2])
        plotter = PlotHandler(translation, df_final, "")

        labels = clusterMaster.full_pipline_tree_hierachy(
            graph, 
            params[4],  # This is now the tree function
            translation,
            plotter,
            params[3],
            1  # Keeping this at 1 as suggested
        )

        nmi = normalized_mutual_info_score(df_final.labels, labels)
        
        # Check if this is a new best NMI score
        if nmi > best_nmi:
            best_nmi = nmi
            print(f"\nNew best NMI found: {best_nmi:.4f}")
            print("Parameters:")
            print(f"  edge_removal_lower: {params[0]}")
            print(f"  edge_removal_upper: {params[1]}")
            print(f"  clique_merge: {params[2]}")
            print(f"  cluster_distance: {params[3]}")
            print(f"  tree_function: {params[4].__name__}")
        
        result = {
            'edge_removal_lower': params[0],
            'edge_removal_upper': params[1],
            'clique_merge': params[2],
            'cluster_distance': params[3],
            'tree_function': params[4].__name__,
            'nmi': nmi
        }
        
        # Keep track of top 20 results
        top_results.append(result)
        top_results.sort(key=lambda x: x['nmi'], reverse=True)
        top_results = top_results[:20]
        

    print("\nTop 20 parameter combinations:")
    for i, result in enumerate(top_results, 1):
        print(f"{i}. NMI: {result['nmi']:.4f}")
        for key, value in result.items():
            if key != 'nmi':
                print(f"   {key}: {value}")
        print()

    return top_results

def plot_top_results(top_results):
    # Prepare data for plotting
    parameter_impact = defaultdict(list)
    for result in top_results:
        for key, value in result.items():
            if key != 'nmi' and key != 'tree_function':
                parameter_impact[key].append((value, result['nmi']))

    # Create subplots
    fig, axs = plt.subplots(2, 2, figsize=(15, 15))
    fig.suptitle('Parameter Impact on NMI Score', fontsize=16)

    for (key, values), ax in zip(parameter_impact.items(), axs.ravel()):
        x, y = zip(*sorted(values))
        ax.plot(x, y, 'o-')
        ax.set_xlabel(key)
        ax.set_ylabel('NMI Score')
        ax.set_title(f'Impact of {key}')

    # Count occurrences of each tree function
    tree_func_count = defaultdict(int)
    for result in top_results:
        tree_func_count[result['tree_function']] += 1

    # Create a bar plot for tree functions
    axs[1, 1].bar(tree_func_count.keys(), tree_func_count.values())
    axs[1, 1].set_xlabel('Tree Function')
    axs[1, 1].set_ylabel('Occurrences in Top 20')
    axs[1, 1].set_title('Tree Function Frequency')
    plt.xticks(rotation=45, ha='right')

    plt.tight_layout()
    plt.savefig('parameter_impact.png')
    print("Plot saved as 'parameter_impact.png'")

# Assuming df_final and translation are already defined
top_results = test_parameters(df_final, translation)

# Plot the results
plot_top_results(top_results)

# Now you can use the best parameters to run your final analysis
best_params = top_results[0]
print("\nRunning final analysis with best parameters...")
graph_base = cc.G.copy()
graph = NxGraphAssistant.remove_edges_with_minor(
    graph_base, 'weight', 
    best_params['edge_removal_lower'],
    best_params['edge_removal_upper']
)

graph = NxGraphAssistant.analyze_cliques(graph, best_params['clique_merge'])
plotter = PlotHandler(translation, df_final, "")

# Get the best tree function
best_tree_function = getattr(Custom_Tree, best_params['tree_function'])

final_labels = clusterMaster.full_pipline_tree_hierachy(
    graph, 
    best_tree_function,
    translation,
    plotter,
    best_params['cluster_distance'],
    1
)

final_nmi = normalized_mutual_info_score(df_final.labels, final_labels)
print(f"Final NMI with best parameters: {final_nmi:.4f}")

Testing Parameters:   0%|          | 2/2240 [00:00<05:42,  6.53combination/s]


New best NMI found: 0.1163
Parameters:
  edge_removal_lower: 0.0
  edge_removal_upper: 0.6
  clique_merge: 0.6
  cluster_distance: 0.5
  tree_function: alex_optimal


Testing Parameters: 100%|██████████| 2240/2240 [09:40<00:00,  3.86combination/s] 



Top 20 parameter combinations:
1. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 0.6
   cluster_distance: 0.5
   tree_function: alex_optimal

2. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 0.6
   cluster_distance: 1.0
   tree_function: alex_optimal

3. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 0.6
   cluster_distance: 1.5
   tree_function: alex_optimal

4. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 0.6
   cluster_distance: 2.0
   tree_function: alex_optimal

5. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 0.6
   cluster_distance: 2.5
   tree_function: alex_optimal

6. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 0.6
   cluster_distance: 3.0
   tree_function: alex_optimal

7. NMI: 0.1163
   edge_removal_lower: 0.0
   edge_removal_upper: 0.6
   clique_merge: 

In [20]:
import itertools
from sklearn.metrics import normalized_mutual_info_score
from tqdm import tqdm
import matplotlib.pyplot as plt
from collections import defaultdict

def test_parameters(df_final, translation):
    # Define parameter ranges
    edge_removal_lower = list(np.arange(0.0, 0.5, 0.05))
    edge_removal_upper = list(np.arange(0.6, 1, 0.1))
    clique_merge = list(np.arange(0.6, 1, 0.05))
    cluster_distance = list(np.arange(0.5, 4, 0.5))
    tree_functions = [
        Custom_Tree.problem_handler_create_multiple_trees_on_conflict,

    ]

    top_results = []
    best_nmi = float('-inf')  # Initialize best_nmi to negative infinity

    # Create a list of valid parameter combinations
    valid_combinations = [
        params for params in itertools.product(edge_removal_lower, edge_removal_upper, clique_merge, cluster_distance, tree_functions)
        if params[0] < params[1]
    ]

    # Use tqdm to create a progress bar
    for params in tqdm(valid_combinations, desc="Testing Parameters", unit="combination"):
        graph_base = cc.G.copy()
        graph = NxGraphAssistant.remove_edges_with_minor(
            graph_base, 'weight', 
            params[0],
            params[1]
        )

        graph = NxGraphAssistant.analyze_cliques(graph, params[2])
        plotter = PlotHandler(translation, df_final, "")

        labels = clusterMaster.full_pipline_tree_hierachy(
            graph, 
            params[4],  # This is now the tree function
            translation,
            plotter,
            params[3],
            1  # Keeping this at 1 as suggested
        )

        nmi = normalized_mutual_info_score(df_final.labels, labels)
        
        # Check if this is a new best NMI score
        if nmi > best_nmi:
            best_nmi = nmi
            print(f"\nNew best NMI found: {best_nmi:.4f}")
            print("Parameters:")
            print(f"  edge_removal_lower: {params[0]}")
            print(f"  edge_removal_upper: {params[1]}")
            print(f"  clique_merge: {params[2]}")
            print(f"  cluster_distance: {params[3]}")
            print(f"  tree_function: {params[4].__name__}")
        
        result = {
            'edge_removal_lower': params[0],
            'edge_removal_upper': params[1],
            'clique_merge': params[2],
            'cluster_distance': params[3],
            'tree_function': params[4].__name__,
            'nmi': nmi
        }
        
        # Keep track of top 20 results
        top_results.append(result)
        top_results.sort(key=lambda x: x['nmi'], reverse=True)
        top_results = top_results[:20]
        

    print("\nTop 20 parameter combinations:")
    for i, result in enumerate(top_results, 1):
        print(f"{i}. NMI: {result['nmi']:.4f}")
        for key, value in result.items():
            if key != 'nmi':
                print(f"   {key}: {value}")
        print()

    return top_results

def plot_top_results(top_results):
    # Prepare data for plotting
    parameter_impact = defaultdict(list)
    for result in top_results:
        for key, value in result.items():
            if key != 'nmi' and key != 'tree_function':
                parameter_impact[key].append((value, result['nmi']))

    # Create subplots
    fig, axs = plt.subplots(2, 2, figsize=(15, 15))
    fig.suptitle('Parameter Impact on NMI Score', fontsize=16)

    for (key, values), ax in zip(parameter_impact.items(), axs.ravel()):
        x, y = zip(*sorted(values))
        ax.plot(x, y, 'o-')
        ax.set_xlabel(key)
        ax.set_ylabel('NMI Score')
        ax.set_title(f'Impact of {key}')

    # Count occurrences of each tree function
    tree_func_count = defaultdict(int)
    for result in top_results:
        tree_func_count[result['tree_function']] += 1

    # Create a bar plot for tree functions
    axs[1, 1].bar(tree_func_count.keys(), tree_func_count.values())
    axs[1, 1].set_xlabel('Tree Function')
    axs[1, 1].set_ylabel('Occurrences in Top 20')
    axs[1, 1].set_title('Tree Function Frequency')
    plt.xticks(rotation=45, ha='right')

    plt.tight_layout()
    plt.savefig('parameter_impact.png')
    print("Plot saved as 'parameter_impact.png'")

# Assuming df_final and translation are already defined
top_results = test_parameters(df_final, translation)

# Plot the results
plot_top_results(top_results)

# Now you can use the best parameters to run your final analysis
best_params = top_results[0]
print("\nRunning final analysis with best parameters...")
graph_base = cc.G.copy()
graph = NxGraphAssistant.remove_edges_with_minor(
    graph_base, 'weight', 
    best_params['edge_removal_lower'],
    best_params['edge_removal_upper']
)

graph = NxGraphAssistant.analyze_cliques(graph, best_params['clique_merge'])
plotter = PlotHandler(translation, df_final, "")

# Get the best tree function
best_tree_function = getattr(Custom_Tree, best_params['tree_function'])

final_labels = clusterMaster.full_pipline_tree_hierachy(
    graph, 
    best_tree_function,
    translation,
    plotter,
    best_params['cluster_distance'],
    1
)

final_nmi = normalized_mutual_info_score(df_final.labels, final_labels)
print(f"Final NMI with best parameters: {final_nmi:.4f}")

Testing Parameters:   0%|          | 2/2240 [00:00<05:20,  6.99combination/s]


New best NMI found: 0.1163
Parameters:
  edge_removal_lower: 0.0
  edge_removal_upper: 0.6
  clique_merge: 0.6
  cluster_distance: 0.5
  tree_function: problem_handler_create_multiple_trees_on_conflict


Testing Parameters:  11%|█▏        | 256/2240 [01:28<11:26,  2.89combination/s]  


KeyboardInterrupt: 

#### Plotting